In [ ]:
# TODO


# Initialise

In [1]:
import pandas as pd
import requests
import numpy as np
import config
api_key = config.api_key

import dill
import plotly.express as px
import cpi
# cpi.update()

In [2]:
%%capture
from tqdm import tqdm_notebook as tqdm
tqdm().pandas()

In [150]:
def list_of_films(start_date, end_date):
    """Query TMDb for movies between two dates.
    
    Will run requests of TMDb API for movies with US theatrical release dates
    between specified dates.  Dates should be given in YYYY-MM-DD format.
    
    Filter out adult movies.  Filter movies that received fewer than 50 votes
    to try and get more populat releases.  Results will be ordered by average
    voter score.  Also filter out documentaries, as we're only interested in
    feature films.
    
    First pull number of pages.  Then cycle through all pages and retrieve 
    full data.
    
    Returns a list of dictionaries.  Each dictionary is one film.
    """
    print(start_date, end_date)
    pages = requests.get('https://api.themoviedb.org/3/discover/movie?api_key=' 
                            +  api_key 
                            + '&primary_release_date.gte=' + start_date
                            + '&primary_release_date.lte=' + end_date
                            + '&include_adult=false' # filter out adult films
                            + '&with_release_type=3&region=US' # select only US theatrical releases
                            + '&sort_by=vote_average.desc' # sort by average vote
                            + '&vote_count.gte=50' # filter films with fewer than 50 votes
                            + '&without_genres=99,9' # filter out documentaries and TV movies
                        ).json()['total_pages']
    print('Number of pages = ', pages)

    films_list = []

    for page in tqdm(range(1, pages+1)):
        response = requests.get('https://api.themoviedb.org/3/discover/movie?api_key=' 
                                +  api_key 
                                + '&primary_release_date.gte=' + start_date
                                + '&primary_release_date.lte=' + end_date
                                + '&include_adult=false' # filter out adult films
                                + '&with_release_type=3&region=US' #select only US theatrical releases
                                + '&sort_by=vote_average.desc' # sort by average vote
                                + '&vote_count.gte=50' # filter films with fewer than 50 votes
                                + '&without_genres=99' # filter out documentaries
                                + '&page={}'.format(page) # page number
                               )
        films = response.json()['results']
        films_list.extend(films)
        
    return films_list

In [4]:
def get_film_details(films):
    films_list = []

    for film in tqdm(films):
        entry = requests.get('https://api.themoviedb.org/3/movie/'
                                   + str(film['id']) 
                                   + '?api_key=' + api_key
                                   + '&language=en-US')
        entry = (entry.json())
        films_list += [entry]
    
    return films_list

In [5]:
def get_film_list_details(films):
    idchunks = [films[x:x + 250] for x in range(0, len(films), 250)]

    filmslist = []
    for ids in tqdm(idchunks):
        results = get_film_details(ids)
        filmslist.extend(results)

    return filmslist

In [140]:
def bin_budget(df):
    bins = [0, 2000000, 5000000, 10000000, 30000000, 50000000, 100000000, 
            250000000, 300000000]
    labels = ['0-2M', '2-5M', '5-10M', '10-30M', '30-50M', '50-100M', '100-250M', '250-300M']
    
    df['budget_bin'] = pd.cut(df['budget'], bins, labels=labels)
    
    return df

In [145]:
def build_films_df(films_list):
    df = pd.DataFrame(films_list).drop(columns=['adult', 'backdrop_path', 'imdb_id',
                                            'homepage', 'overview',
                                            'poster_path', 'tagline'])
    
    df['release_date'] = pd.to_datetime(df['release_date'])

    df['year'] = df['release_date'].dt.year

    df['decade'] = ((df.year)//10)*10
    
    df['budget_adj'] = df[df['year'] != 2019] \
        .apply(lambda x: cpi.inflate(x['budget'], x['year']), axis=1)

    df['revenue_adj'] = df[df['year'] != 2019] \
        .apply(lambda x: cpi.inflate(x['revenue'], x['year']), axis=1)
    
    df['budget_bin'] = bin_budget(df)
    
    return df

In [ ]:
# Request for a specific movie:
# requests.get('https://api.themoviedb.org/3/movie/'
#                                + '10994' 
#                                + '?api_key=' + api_key
#                                + '&language=en-US').json()

# Get 1990s films

Find the list of films for the 1990s

In [151]:
films = list_of_films('1990-01-01', '1999-12-31')

1990-01-01 1999-12-31
Number of pages =  84


Pull the full details on each film

In [62]:
films_list = get_film_list_details(films[0:10])

In [63]:
df_1990s = build_films_df(films_list)

Pickle result

In [818]:
with open('pickles/df_1990s.pkl', 'wb') as file:
    dill.dump(df_1990s, file)

Unpickle result with the following:

In [54]:
with open('pickles/df_1990s.pkl', 'rb') as file:
    df_1990s = dill.load(file)

## Plot some results

In [451]:
df_1990s.columns

Index(['belongs_to_collection', 'budget', 'genres', 'id', 'original_language',
       'original_title', 'popularity', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'title', 'video', 'vote_average',
       'vote_count', 'year', 'month', 'day'],
      dtype='object')

In [456]:
fig = px.scatter(df_1990s[df_1990s['budget']>0], x='budget', y='vote_average', hover_name='title')
fig.show()

In [453]:
fig = px.scatter(df_1990s[df_1990s['budget']>0], x='budget', y='revenue', color='year', hover_name='title')
fig.show()

In [454]:
fig = px.box(df_1990s[df_1990s['budget']>0], x='year', y='budget')
fig.show()

In [455]:
fig = px.histogram(df_1990s[df_1990s['budget']>0], x='budget', y='runtime', color='year', nbins=40, histfunc='avg')
fig.show()

In [283]:
fig = px.histogram(df[df['vote_count']<=100], x='vote_count', nbins=100, color='title')
fig.show()

# Get 2000s

Find the list of films for the 2000s

In [152]:
films = list_of_films('2000-01-01', '2009-12-31')

2000-01-01 2009-12-31
Number of pages =  156


Pull the full details on each film

In [155]:
films_list = get_film_list_details(films[2440:])

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [156]:
df_2000s = build_films_df(films_list)

TypeError: ('Years can only be converted to other years. Months only to other months.', 'occurred at index 0')

Pickle result

In [157]:
with open('pickles/df_2000s.pkl', 'wb') as file:
    dill.dump(df_2000s, file)

NameError: name 'df_2000s' is not defined

Unpickle result with the following:

In [158]:
with open('pickles/df_2000s.pkl', 'rb') as file:
    df_2000s = dill.load(file)

EOFError: Ran out of input

## Plot some results

In [159]:
highest_revenue = df_2000s.sort_values('revenue', ascending=False)[0:1000]

NameError: name 'df_2000s' is not defined

In [160]:
fig = px.box(highest_revenue[highest_revenue['budget']>0], x='year', y='budget',
             hover_data=['title'], points='all')
fig.show()

NameError: name 'highest_revenue' is not defined

In [161]:
fig = px.scatter(df_2000s[df_2000s['budget']>0], x='budget', y='revenue', color='year', hover_name='title')
fig.show()

NameError: name 'df_2000s' is not defined

Number of films in budget categories over time?

In [162]:
df_2000s

NameError: name 'df_2000s' is not defined

In [163]:
grouped = df_2000s.groupby(['year', 'budget_bin']).count()

NameError: name 'df_2000s' is not defined

In [164]:
grouped

NameError: name 'grouped' is not defined

In [ ]:
grouped.reset_index()

In [165]:
fig = px.line(grouped.reset_index(), x='year', y='id', color='budget_bin')
fig.show()

NameError: name 'grouped' is not defined

# Get 2010s

Find the list of films for the 2010s

In [166]:
films = list_of_films('2010-01-01', '2019-12-31')

2010-01-01 2019-12-31
Number of pages =  181


In [167]:
films

[{'popularity': 42.963,
  'vote_count': 5152,
  'video': False,
  'poster_path': '/iiZZdoQBEYBv6id8su7ImL0oCbD.jpg',
  'id': 324857,
  'adult': False,
  'backdrop_path': '/uUiId6cG32JSRI6RyBQSvQtLjz2.jpg',
  'original_language': 'en',
  'original_title': 'Spider-Man: Into the Spider-Verse',
  'genre_ids': [28, 12, 16, 35, 878],
  'title': 'Spider-Man: Into the Spider-Verse',
  'vote_average': 8.4,
  'overview': 'Miles Morales is juggling his life between being a high school student and being a spider-man. When Wilson "Kingpin" Fisk uses a super collider, others from across the Spider-Verse are transported to this dimension.',
  'release_date': '2018-12-14'},
 {'popularity': 27.997,
  'id': 244786,
  'video': False,
  'vote_count': 8306,
  'vote_average': 8.4,
  'title': 'Whiplash',
  'release_date': '2014-10-10',
  'original_language': 'en',
  'original_title': 'Whiplash',
  'genre_ids': [18, 10402],
  'backdrop_path': '/6bbZ6XyvgfjhQwbplnUh1LSj1ky.jpg',
  'adult': False,
  'overview':

Pull the full details on each film

In [168]:
example = requests.get('https://api.themoviedb.org/3/movie/'
                               + '239459' 
                               + '?api_key=' + api_key
                               + '&language=en-US').json()

In [169]:
films_list = get_film_list_details(films)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [ ]:
df_2010s = build_films_df(films_list)

Pickle result

In [ ]:
with open('pickles/df_2010s.pkl', 'wb') as file:
    dill.dump(df_2010s, file)

Unpickle result with the following:

In [795]:
with open('pickles/df_2010s.pkl', 'rb') as file:
    df_2010s = dill.load(file)

## Plot some results

In [801]:
highest_revenue = df_2010s.sort_values('revenue', ascending=False)[0:1000]

In [802]:
fig = px.box(highest_revenue[highest_revenue['budget']>0], x='year', y='budget',
             hover_data=['title'], points='all')
fig.show()

In [803]:
fig = px.scatter(df_2010s[df_2010s['budget']>0], x='budget', y='revenue', color='year', hover_name='title')
fig.show()

In [809]:
grouped = df_2010s.groupby(['year', 'budget_bin']).count()

In [810]:
fig = px.line(grouped.reset_index(), x='year', y='id', color='budget_bin')
fig.show()

# Check all decades

In [859]:
all_films = pd.concat([df_1990s, df_2000s, df_2010s], axis=0, sort=False)

In [860]:
genres = all_films['genres'].apply(pd.Series) \
            .applymap(lambda x: x.get('name', np.nan) \
                  if isinstance(x, dict) else np.nan)

all_films = all_films.merge(genres, left_index=True, right_index=True)

In [871]:
genres[1].value_counts()

Drama              1360
Thriller            834
Comedy              820
Romance             639
Adventure           495
Action              430
Crime               399
Horror              366
Family              361
Fantasy             257
Science Fiction     249
Animation           219
Mystery             207
History             151
Music               110
War                  50
Western              21
Documentary          15
TV Movie              9
Name: 1, dtype: int64

In [861]:
all_films = all_films[(all_films[0] != 'Documentary|TV Movie')
                    & (all_films[1] != 'Documentary|TV Movie')
                    & (all_films[2] != 'Documentary|TV Movie')
                    & (all_films[3] != 'Documentary|TV Movie')
                    & (all_films[4] != 'Documentary|TV Movie')
                    & (all_films[5] != 'Documentary|TV Movie')
                    & (all_films[6] != 'Documentary|TV Movie')
                    & (all_films[7] != 'Documentary|TV Movie')
                    & (all_films[8] != 'Documentary|TV Movie')] \
            .drop(columns=[0,1,2,3,4,5,6,7,8]) \
            .reset_index(drop=True)

In [862]:
bins = [1, 2000000, 5000000, 10000000, 30000000, 50000000, 100000000, 
        250000000, 300000000]
labels = ['<2M', '2-5M', '5-10M', '10-30M', '30-50M', '50-100M', '100-250M', '250-300M']

all_films['budget_adj_bin'] = pd.cut(all_films['budget_adj'], bins, labels=labels)

In [863]:
grouped = all_films.groupby(['year', 'budget_adj_bin']).count()

In [864]:
fig = px.line(grouped.reset_index(), x='year', y='id', color='budget_adj_bin')
fig.show()

In [865]:
fig = px.box(all_films[all_films['budget']>0], x='year', y='budget_adj')
fig.show()

## Pickle result

In [872]:
with open('pickles/all_films.pkl', 'wb') as file:
    dill.dump(all_films, file)

# Compare Scorsese to the Coen Bros

Find the person codes for Martin Scorsese and the Coen brothers. We'll use Ethan, just because we need one of them.

In [7]:
response = requests.get('https://api.themoviedb.org/3/search/person?api_key=' 
                            +  api_key 
                            + '&include_adult=false' # filter out adult films
                            + '&language=en-US'
                            + '&query=ethan%coen'
                           ).json()
response

{'page': 1,
 'total_results': 1,
 'total_pages': 1,
 'results': [{'popularity': 7.967,
   'known_for_department': 'Writing',
   'name': 'Ethan Coen',
   'id': 1224,
   'profile_path': '/AH5YwNZC5txyJKyjVZhA4ZXFzP.jpg',
   'adult': False,
   'known_for': [{'poster_path': '/nBaqryObPuxmuAndWUjDE5rriTd.jpg',
     'vote_count': 6231,
     'video': False,
     'media_type': 'movie',
     'id': 6977,
     'adult': False,
     'backdrop_path': '/7hx7ANh11TbbvHLDXUuywYkg5rK.jpg',
     'original_language': 'en',
     'original_title': 'No Country for Old Men',
     'genre_ids': [80, 18, 53],
     'title': 'No Country for Old Men',
     'vote_average': 7.9,
     'overview': 'Llewelyn Moss stumbles upon dead bodies, $2 million and a hoard of heroin in a Texas desert, but methodical killer Anton Chigurh comes looking for it, with local sheriff Ed Tom Bell hot on his trail. The roles of prey and predator blur as the violent pursuit of money and justice collide.',
     'release_date': '2007-11-08'},

In [109]:
directors = {'scorsese': '1032',
             'coen': '1224'}

## Martin Scorsese data

In [20]:
def director_request(director):
    response = requests.get('https://api.themoviedb.org/3/person/'
                            + director + '/'
                            + 'movie_credits/'        
                            + '?api_key=' + api_key
                            + '&language=en-US')
    
    director_df = pd.DataFrame((response.json())['crew']) \
                    .drop(columns=['adult', 
                                   'backdrop_path',
                                   'poster_path',
                                   'credit_id',])
    
    return director_df

In [104]:
def films_list_df(list_of_films):
    
    films_list = []

    for film in tqdm(list_of_films):
        entry = requests.get('https://api.themoviedb.org/3/movie/'
                                   + str(film) 
                                   + '?api_key=' + api_key
                                   + '&language=en-US')
        entry = (entry.json())
        films_list += [entry]
        
    df = pd.DataFrame(films_list) \
            .drop(columns=['adult', 'backdrop_path', 'imdb_id',
                           'homepage', 'overview',
                           'poster_path', 'tagline'])
    
    df['release_date'] = pd.to_datetime(df['release_date'])
    
    df = df[df['status'] == 'Released']
    
    df['year'] = df['release_date'].dt.year

    df['decade'] = ((df.year)//10)*10
    
    df['budget_adj'] = df[(df['year'] != 2019) & (df['status'] == 'Released')] \
        .apply(lambda x: cpi.inflate(x['budget'], x['year']), axis=1)

    df['revenue_adj'] = df[df['year'] != 2019] \
        .apply(lambda x: cpi.inflate(x['revenue'], x['year']), axis=1)
    
    return df

In [21]:
scorsese = director_request(directors['scorsese'])

We want the list of films Scorsese directed. First filter those out of the dataframe, then get the list of ids.

In [23]:
scorsese_list = scorsese[scorsese['job'] == 'Director']['id'].to_list()

Run a query for each film in the list.

In [105]:
scorsese_df = films_list_df(scorsese_list)

In [106]:
scorsese_df

belongs_to_collection     budget  \
0                                                None    1300000   
1                                                None     500000   
2                                                None   20000000   
3                                                None          0   
4                                                None   52000000   
5                                                None   25000000   
6                                                None   90000000   
7                                                None   18000000   
8                                                None   35000000   
9                                                None  110000000   
10                                               None   34000000   
11                                               None  100000000   
12                                               None    4500000   
13                                               None    7000000   
14                                               None          0   
15                                               None   80000000   
16                                               None     600000   
17                                               None          0   
18  {'id': 387219, 'name': 'The Hustler Collection...   13800000   
19                                               None   32000000   
20                                               None   14000000   
21                                               None   15000000   
22                                               None     155000   
23                                               None   28000000   
24                                               None          0   
25                                               None          0   
26                                               None          0   
27                                               None  170000000   
28                                               None          0   
29                                               None          0   
30                                               None          0   
31                                               None          0   
32                                               None    2000000   
33                                               None          0   
34                                               None          0   
35                                               None          0   
36                                               None          0   
37                                               None          0   
38                                               None  100000000   
39                                               None          0   
40                                               None          0   
41                                               None    2000000   
42                                               None          0   
44                                               None          0   
45                                               None          0   
46                                               None          0   
47                                               None   46000000   
50                                               None          0   
51                                               None          0   
52                                               None          0   
53                                               None          0   
54                                               None          0   
55                                               None          0   
56                                               None          0   
57                                               None          0   
58                                               None          0   

                                               genres      id  \
0   [{'id': 80, 'name': 'Crime'}, {'id': 18, 'name...     103   
1   [{'id': 18, 'name': '

## Coen Bros data

In [110]:
coens = director_request(directors['coen'])

In [111]:
coens_list = coens[coens['job'] == 'Director']['id'].to_list()

In [112]:
coens_df = films_list_df(coens_list)

## Combine directors

In [127]:
scorsese_df['director'] = 'Scorsese'

In [128]:
coens_df['director'] = 'Coens'

In [132]:
directors = pd.concat([scorsese_df, coens_df]).reset_index(drop=True)

In [474]:
with open('pickles/scorsese_coens.pkl', 'wb') as file:
    dill.dump(directors, file)

In [130]:
directors.columns

Index(['index', 'belongs_to_collection', 'budget', 'genres', 'id',
       'original_language', 'original_title', 'popularity',
       'production_companies', 'production_countries', 'release_date',
       'revenue', 'runtime', 'spoken_languages', 'status', 'title', 'video',
       'vote_average', 'vote_count', 'year', 'decade', 'budget_adj',
       'revenue_adj', 'director'],
      dtype='object')

In [133]:
directors.sort_values('year', ascending=False)

belongs_to_collection     budget  \
55                                               None          0   
65                                               None          0   
46                                               None   46000000   
64                                               None   22000000   
3                                                None          0   
39                                               None          0   
38                                               None  100000000   
63                                               None   11000000   
37                                               None          0   
27                                               None  170000000   
15                                               None   80000000   
29                                               None          0   
34                                               None          0   
62                                               None   38000000   
60                                               None    7000000   
17                                               None          0   
56                                               None   37000000   
14                                               None          0   
59                                               None   25000000   
61                                               None          0   
58  {'id': 626668, 'name': 'Cities of Love', 'post...   13000000   
6                                                None   90000000   
32                                               None    2000000   
57                                               None          0   
50                                               None          0   
9                                                None  110000000   
49                                               None          0   
48                                               None          0   
44                                               None          0   
75                                               None   60000000   
..                                                ...        ...   
68                                               None    9000000   
47                                               None          0   
69                                               None   14000000   
40                                               None          0   
5                                                None   25000000   
21                                               None   15000000   
54                                               None          0   
13                                               None    7000000   
70                                               None    6000000   
41                                               None    2000000   
18  {'id': 387219, 'name': 'The Hustler Collection...   13800000   
12                                               None    4500000   
71                                               None    1500000   
2                                                None   20000000   
7                                                None   18000000   
22                                               None     155000   
25                                               None          0   
20                                               None   14000000   
0                                                None    1300000   
35                                               None          0   
28                                               None          0   
1                                                None     500000   
16                                               None     600000   
45                                               None          0   
43                                               None          0   
30                                               None          0   
52                                               None          0   
26                  

## Plot some results

In [134]:
fig = px.scatter(directors[directors['budget']>0], x='budget', y='budget_adj',
                 color='director', hover_name='title')
fig.show()

In [135]:
fig = px.scatter(directors[directors['budget']>0], x='budget', y='revenue', 
                 color='director', hover_name='title')
fig.show()

In [137]:
fig = px.box(directors[directors['budget']>0], x='decade', y='budget',
             color='director')
fig.show()

In [138]:
fig = px.box(directors[directors['budget']>0], x='decade', y='budget_adj',
             color='director')
fig.show()

In [139]:
fig = px.bar(directors[directors['budget']>0], x='decade', y='budget',
                   color='director', barmode='group')
fig.show()